In [1]:
import pandas as pd
import numpy as np
import seaborn.objects as so
import json
from pathlib import Path
from nps import io


## File Structure

in npe2api:
- public/
  - conda/ # specific files for each conda package
  - github/ # branch, issues, PRs, forks, stars, archived, last commit, etc <-- seems quite out of date
  - manifest/ # contains the napari.yaml manifests for each plugin
  - pypi/ # specific files
    - trove classifer
    - author
    - downloads?? maybe
    - release history
    - license
    - requirements
    - requires_python
    - recent release
- classifiers.json # active or withdraw, what pypi versions exist, and the name
- extended_summary.json # summary of:
  - name
  - current version
  - pypi versions
  - author
  - license
  - links
  - seems to exclude withdrawn or deleted plugins

So it looks like I will need to investigate classifiers and extended summary for some basic info, but then crawl specifically each pypi file for more detailed info (like python version, dependences, etc).

In [2]:
NPE2API_DATA = Path("../npe2api/public")
OUTPUT_DIR = Path("reports")
OUTPUT_DIR.mkdir(exist_ok=True)

if NPE2API_DATA.exists():
    pypi_files = list(NPE2API_DATA.glob("pypi/*.json"))
    conda_files = list(NPE2API_DATA.glob("conda/*.json"))
    summary_df = io.load_json_as_dataframe(NPE2API_DATA / "extended_summary.json")
    classifiers_df = io.load_json_as_dataframe(NPE2API_DATA / "classifiers.json")



In [ ]:
status_cols = ['active', 'withdrawn', 'deleted']

classifiers_df[status_cols] = classifiers_df[status_cols].fillna(False).astype(bool)

classifiers_status = classifiers_df[status_cols].idxmax(axis=1)
# classifiers_status[classifiers_status != 'active']  # Show non-active packages
classifiers_status.value_counts()

active       573
withdrawn     33
Name: count, dtype: int64

In [10]:
classifiers_df

active  withdrawn  deleted     status
acquifer-napari            True      False    False     active
affinder                   True      False    False     active
allencell-segmenter-ml     True      False    False     active
alveoleye                  True      False    False     active
anchor-droplet-chip        True      False    False     active
...                         ...        ...      ...        ...
nd2-dask                  False       True    False  withdrawn
ome-zarr                  False       True    False  withdrawn
pyclesperanto-prototype   False       True    False  withdrawn
tracktour                 False       True    False  withdrawn
napari-sim-simulator      False      False    False     active

[606 rows x 4 columns]

Set up PyPi data

In [ ]:
pypi_data = {}
for file in pypi_files:
    plugin_name = file.stem
    pypi_data[plugin_name] = io.load_json(file)

pypi_df = pd.DataFrame.from_dict(pypi_data, orient='index')
pypi_df

info  \
acquifer-napari         {'author': 'Laurent Thomas', 'author_email': '...   
affinder                {'author': 'Juan Nunez-Iglesias', 'author_emai...   
allencell-segmenter-ml  {'author': None, 'author_email': None, 'bugtra...   
alveoleye               {'author': 'Joseph Hirsh', 'author_email': 'jo...   
anchor-droplet-chip     {'author': 'Andrey Aristov', 'author_email': '...   
...                                                                   ...   
workshop-demo           {'author': 'Draga Doncila Pop', 'author_email'...   
world2data              {'author': 'Marc Boucsein, Robin Koch', 'autho...   
yt-napari               {'author': 'Chris Havlin', 'author_email': 'ch...   
zarpaint                {'author': 'Abigail S McGovern and Juan Nunez-...   
zarr-tools              {'author': 'Andrey Aristov', 'author_email': '...   

                        last_serial  \
acquifer-napari            22057882   
affinder                   30239145   
allencell-segmenter-ml     31400556   
alveoleye                  30222067   
anchor-droplet-chip        24206867   
...                             ...   
workshop-demo              13143987   
world2data                 12575042   
yt-napari                  23349457   
zarpaint                   23856378   
zarr-tools                 17179913   

                                                                 releases  \
acquifer-napari         {'0.0.1': [{'comment_text': '', 'digests': {'b...   
affinder                {'0.1.0': [{'comment_text': '', 'digests': {'b...   
allencell-segmenter-ml  {'0.1.16': [{'comment_text': '', 'digests': {'...   
alveoleye               {'0.1.2': [{'comment_text': '', 'digests': {'b...   
anchor-droplet-chip     {'0.2.0': [{'comment_text': '', 'digests': {'b...   
...                                                                   ...   
workshop-demo           {'0.0.1': [{'comment_text': '', 'digests': {'b...   
world2data              {'0.0.3': [{'comment_text': '', 'digests': {'b...   
yt-napari               {'0.0.1': [{'comment_text': '', 'digests': {'b...   
zarpaint                {'0.1.0': [{'comment_text': '', 'digests': {'b...   
zarr-tools              {'0.4.2': [{'comment_text': '', 'digests': {'b...   

                                                                     urls  \
acquifer-napari         [{'comment_text': '', 'digests': {'blake2b_256...   
affinder                [{'comment_text': None, 'digests': {'blake2b_2...   
allencell-segmenter-ml  [{'comment_text': None, 'digests': {'blake2b_2...   
alveoleye               [{'comment_text': None, 'digests': {'blake2b_2...   
anchor-droplet-chip     [{'comment_text': '', 'digests': {'blake2b_256...   
...                                                                   ...   
workshop-demo           [{'comment_text': '', 'digests': {'blake2b_256...   
world2data              [{'comment_text': '', 'digests': {'blake2b_256...   
yt-napari               [{'comment_text': '', 'digests': {'blake2b_256...   
zarpaint                [{'comment_text': '', 'digests': {'blake2b_256...   
zarr-tools              [{'comment_text': '', 'digests': {'blake2b_256...   

                       vulnerabilities  
acquifer-napari                     []  
affinder                            []  
allencell-segmenter-ml              []  
alveoleye                           []  
anchor-droplet-chip                 []  
...                                ...  
workshop-demo                       []  
world2data                          []  
yt-napari                           []  
zarpaint                            []  
zarr-tools                          []  

[612 rows x 5 columns]

In [11]:
# add the classifier_df['status'] status to the pypi dataframe
pypi_df['status'] = classifiers_status
pypi_df

info  \
acquifer-napari         {'author': 'Laurent Thomas', 'author_email': '...   
affinder                {'author': 'Juan Nunez-Iglesias', 'author_emai...   
allencell-segmenter-ml  {'author': None, 'author_email': None, 'bugtra...   
alveoleye               {'author': 'Joseph Hirsh', 'author_email': 'jo...   
anchor-droplet-chip     {'author': 'Andrey Aristov', 'author_email': '...   
...                                                                   ...   
workshop-demo           {'author': 'Draga Doncila Pop', 'author_email'...   
world2data              {'author': 'Marc Boucsein, Robin Koch', 'autho...   
yt-napari               {'author': 'Chris Havlin', 'author_email': 'ch...   
zarpaint                {'author': 'Abigail S McGovern and Juan Nunez-...   
zarr-tools              {'author': 'Andrey Aristov', 'author_email': '...   

                        last_serial  \
acquifer-napari            22057882   
affinder                   30239145   
allencell-segmenter-ml     31400556   
alveoleye                  30222067   
anchor-droplet-chip        24206867   
...                             ...   
workshop-demo              13143987   
world2data                 12575042   
yt-napari                  23349457   
zarpaint                   23856378   
zarr-tools                 17179913   

                                                                 releases  \
acquifer-napari         {'0.0.1': [{'comment_text': '', 'digests': {'b...   
affinder                {'0.1.0': [{'comment_text': '', 'digests': {'b...   
allencell-segmenter-ml  {'0.1.16': [{'comment_text': '', 'digests': {'...   
alveoleye               {'0.1.2': [{'comment_text': '', 'digests': {'b...   
anchor-droplet-chip     {'0.2.0': [{'comment_text': '', 'digests': {'b...   
...                                                                   ...   
workshop-demo           {'0.0.1': [{'comment_text': '', 'digests': {'b...   
world2data              {'0.0.3': [{'comment_text': '', 'digests': {'b...   
yt-napari               {'0.0.1': [{'comment_text': '', 'digests': {'b...   
zarpaint                {'0.1.0': [{'comment_text': '', 'digests': {'b...   
zarr-tools              {'0.4.2': [{'comment_text': '', 'digests': {'b...   

                                                                     urls  \
acquifer-napari         [{'comment_text': '', 'digests': {'blake2b_256...   
affinder                [{'comment_text': None, 'digests': {'blake2b_2...   
allencell-segmenter-ml  [{'comment_text': None, 'digests': {'blake2b_2...   
alveoleye               [{'comment_text': None, 'digests': {'blake2b_2...   
anchor-droplet-chip     [{'comment_text': '', 'digests': {'blake2b_256...   
...                                                                   ...   
workshop-demo           [{'comment_text': '', 'digests': {'blake2b_256...   
world2data              [{'comment_text': '', 'digests': {'blake2b_256...   
yt-napari               [{'comment_text': '', 'digests': {'blake2b_256...   
zarpaint                [{'comment_text': '', 'digests': {'blake2b_256...   
zarr-tools              [{'comment_text': '', 'digests': {'blake2b_256...   

                       vulnerabilities  status  
acquifer-napari                     []  active  
affinder                            []  active  
allencell-segmenter-ml              []  active  
alveoleye                           []  active  
anchor-droplet-chip                 []  active  
...                                ...     ...  
workshop-demo                       []  active  
world2data                          []  active  
yt-napari                           []  active  
zarpaint                            []  active  
zarr-tools                          []  active  

[612 rows x 6 columns]

In [12]:
pypi_info = pd.json_normalize(pypi_df['info'])
pypi_info

author  \
0                                Laurent Thomas   
1                           Juan Nunez-Iglesias   
2                                          None   
3                                  Joseph Hirsh   
4                                Andrey Aristov   
..                                          ...   
607                           Draga Doncila Pop   
608                   Marc Boucsein, Robin Koch   
609                                Chris Havlin   
610  Abigail S McGovern and Juan Nunez-Iglesias   
611                              Andrey Aristov   

                                  author_email bugtrack_url  \
0                                                      None   
1               juan.nunez-iglesias@monash.edu         None   
2                                         None         None   
3                       josephhirsh9@gmail.com         None   
4                          aaristov@pasteur.fr         None   
..                                         ...          ...   
607  ddoncilapop@contractor.chanzuckerberg.com         None   
608                                                    None   
609                     chris.havlin@gmail.com         None   
610             juan.nunez-iglesias@monash.edu         None   
611                        aaristov@pasteur.fr         None   

                                           classifiers  \
0    [Framework :: napari, License :: OSI Approved ...   
1    [Development Status :: 3 - Alpha, Framework ::...   
2    [Development Status :: 2 - Pre-Alpha, Framewor...   
3    [Development Status :: 2 - Pre-Alpha, Framewor...   
4    [Development Status :: 2 - Pre-Alpha, Framewor...   
..                                                 ...   
607  [Development Status :: 2 - Pre-Alpha, Framewor...   
608  [Development Status :: 4 - Beta, Framework :: ...   
609  [Development Status :: 2 - Pre-Alpha, Framewor...   
610  [Development Status :: 4 - Beta, Framework :: ...   
611  [Development Status :: 2 - Pre-Alpha, Framewor...   

                                           description  \
0    # acquifer-napari\r\n\r\nThe acquifer-napari p...   
1    # Description\n\nThis GUI plugin allows you to...   
2    # Allencell-segmenter-ml\n\n[![Test and lint](...   
3    # AlveolEye: Automated Lung Morphometry Made E...   
4    # ⚓ anchor-droplet-chip\n## Measuring single-c...   
..                                                 ...   
607  # workshop-demo\n\n[![License](https://img.shi...   
608  # World2Data\n\n[![License](https://img.shield...   
609  # yt-napari\n\n[![License](https://img.shields...   
610  # zarpaint\n\n[![License](https://img.shields....   
611  # zarr-tools\n\nConvert nd2 to zarr\n\n[![Lice...   

    description_content_type docs_url download_url         dynamic  \
0              text/markdown     None                         None   
1              text/markdown     None         None  [License-File]   
2              text/markdown     None         None  [License-File]   
3              text/markdown     None         None  [License-File]   
4              text/markdown     None         None            None   
..                       ...      ...          ...             ...   
607            text/markdown     None                         None   
608            text/markdown     None                         None   
609            text/markdown     None         None            None   
610            text/markdown     None         None            None   
611            text/markdown     None                         None   

                                            home_page  ...  \
0                                                      ...   
1                     https://github.com/jni/affinder  ...   
2                                                None  ...   
3                                                None  ...   
4    https://github.com/BaroudLab/anchor-driplet-chip  ...   
..                                                ...  ...   
60